## 미디 파일에 맞는 스타일 벡터 생성을 위한 곳

In [ ]:
from music21 import note, chord
from music21.stream.base import Score

def score_to_style_vector(score: Score) -> dict:
    """MIDI 파일(music21 score)을 분석하여 스타일 벡터를 생성하는 함수"""

    score.show('midi')

    # 1. Key & Mode
    key_obj = score.analyze("key")
    key = key_obj.tonic.name # type: ignore
    mode = key_obj.mode # type: ignore

    # 2. 멜로디 음표 리스트 추출
    melody_notes = [n for n in score.flat.notes if isinstance(n, note.Note)]
    pitches = [n.pitch.midi for n in melody_notes]
    onsets = [n.offset for n in melody_notes]

    # 3. 코드 (화성) 분석
    chords = [c for c in score.flat.getElementsByClass(chord.Chord)]
    complex_chords = sum([1 for c in chords if len(c.pitches) > 3])
    chord_complexity = complex_chords / (len(chords) + 1e-6)  # 비율

    # 4. 멜로디 밀도 (단위 박자당 노트 수)
    melody_density = len(melody_notes) / (score.highestTime + 1e-6) # type: ignore

    # 5. 싱코페이션 (off-beat 비율: 1/4 박자 단위 기준)
    syncopation = sum([1 for o in onsets if (o % 1) != 0]) / (len(onsets) + 1e-6)

    # 6. 피치 범위
    pitch_range = max(pitches) - min(pitches) if pitches else 0

    # 7. 사람이 생각하는 곡의 분위기
    mood = input("분위기 입력 (이 중에서 선택: Happy, Chill, Emotional, Aggressive, Dreamy, Melodic): ")

    # 스타일 벡터 결과
    style_vector = {
        "bpm": 128,  # 기본값 설정
        "key": key,
        "mode": mode,
        "chord_complexity": round(chord_complexity, 3),
        "melody_density": round(melody_density, 3),
        "syncopation": round(syncopation, 3),
        "pitch_range": pitch_range,
        "mood": mood
    }

    return style_vector

In [ ]:
from HarmonyMIDIToken import HarmonyMIDIToken as Tokenizer
import os

#tokenized_data = []

for filename in os.listdir("data"):
    if filename.endswith(".mid") and not filename in [i["name"] for i in tokenized_data]:
        MIDI = Tokenizer()
        print(f"file name: {filename}")
        MIDI.set_midi(os.path.join("data", filename))
        
        vector = score_to_style_vector(MIDI.to_midi()) # type: ignore
    
        tokenized_data.append({
            "name": filename,
            "vector":vector,
            "token":MIDI.token_id
            })
    else:
        print(f"Skipping non-MIDI or already Done file: {filename}")
    

Skipping non-MIDI file: 0.mid
Skipping non-MIDI file: 1.mid
Skipping non-MIDI file: 10.mid
Skipping non-MIDI file: 11.mid
Skipping non-MIDI file: 12.mid
Skipping non-MIDI file: 13.mid
Skipping non-MIDI file: 14.mid
Skipping non-MIDI file: 15.mid
Skipping non-MIDI file: 16.mid
Skipping non-MIDI file: 17.mid
Skipping non-MIDI file: 18.mid
Skipping non-MIDI file: 19.mid
Skipping non-MIDI file: 2.mid
Skipping non-MIDI file: 20.mid
Skipping non-MIDI file: 21.mid
Skipping non-MIDI file: 22.mid
Skipping non-MIDI file: 23.mid
Skipping non-MIDI file: 24.mid
Skipping non-MIDI file: 25.mid
Skipping non-MIDI file: 26.mid
Skipping non-MIDI file: 27.mid
Skipping non-MIDI file: 28.mid
Skipping non-MIDI file: 29.mid
Skipping non-MIDI file: 3.mid
Skipping non-MIDI file: 30.mid
Skipping non-MIDI file: 31.mid
Skipping non-MIDI file: 32.mid
Skipping non-MIDI file: 33.mid
Skipping non-MIDI file: 4.mid
Skipping non-MIDI file: 5.mid
Skipping non-MIDI file: 6.mid
Skipping non-MIDI file: 7.mid
Skipping non-MID

In [2]:
print("Tokenized MIDI data:", len(tokenized_data))

Tokenized MIDI data: 34


In [5]:
import json # JSON 파일로 토크나이저 미디 데이터 저장

with open('tokenized_midi_data.json', 'w') as f:
    json.dump(tokenized_data, f, indent=4)

In [8]:
import json # JSON으로 저장한 토크나이저 미디 데이터 불러오기

with open('tokenized_midi_data.json', 'r') as f:
    tokenized_data = json.load(f)

## 데이터 수정

In [ ]:
from HarmonyMIDIToken import HarmonyMIDIToken as Tokenizer

for item in tokenized_data:
    if item['vector']['mood'] == "IDK":
        MIDI = Tokenizer()
        
        MIDI.set_id(item['token'])
        MIDI.to_midi().show('midi')
        item['vector']['mood'] = input("분위기 재 입력")

In [4]:
for item in tokenized_data:
    if not "name" in item.keys():
        print(item)
        item['name'] = item['vector']
        item.pop('vector')

In [ ]:
from HarmonyMIDIToken import HarmonyMIDIToken as Tokenizer
import os

for item in tokenized_data:
    filename = item['name']

    MIDI = Tokenizer()
    MIDI.set_midi(os.path.join("data", filename))

    try:
        item['token'] = MIDI.token_id
    except:
        print(f"{item['name']} 을 토크나이즈 하는데 실패함.")

ValueError: min() arg is an empty sequence

## 데이터 전처리

In [9]:
from sklearn.preprocessing import OneHotEncoder, MinMaxScaler
from sklearn.compose import ColumnTransformer
import torch
import pandas as pd

vector_df = pd.DataFrame([item['vector'] for item in tokenized_data])

tokens = [item['token'] for item in tokenized_data]

# 전처리 파이프라인
preprocessor = ColumnTransformer([
    ("cat", OneHotEncoder(sparse_output=False), ["mode", "mood", "key"]),
    ("num", MinMaxScaler(), ["bpm", "chord_complexity", "melody_density", "syncopation", "pitch_range"])
])

X = preprocessor.fit_transform(vector_df)

# # 토큰 시퀀스 패딩 (-1으로 뒤에 채우기)
# max_len = max(len(seq) for seq in tokens)
# padded_tokens = [seq + [-1]*(max_len - len(seq)) for seq in tokens]

# # 각 샘플의 실제 길이
# lengths = torch.tensor([len(seq) for seq in tokens], dtype=torch.long)

# Tensor 변환
#X_tensor = torch.tensor(X, dtype=torch.float32)
#Y_tensor = torch.tensor(padded_tokens, dtype=torch.long)
print(tokens)

[[[81, 3, 65, 1, 3, 53, 3], [0, 1, 0, 1, 1, 0, 1], [81, 2, 65, 1, 2, 53, 2], [0, 1, 0, 1, 1, 0, 1], [81, 1, 65, 1, 1, 53, 1], [0, 1, 0, 1, 1, 0, 1], [79, 2, 65, 1, 2, 53, 2], [0, 1, 0, 1, 1, 0, 1], [79, 2, 65, 1, 2, 53, 2], [0, 1, 0, 1, 1, 0, 1], [84, 1, 60, 8, 1, 55, 1], [84, 2, 60, 8, 2, 55, 2], [0, 2, 0, 1, 2, 0, 2], [84, 2, 60, 8, 2, 55, 2], [83, 1, 60, 8, 1, 55, 1], [84, 2, 60, 8, 2, 55, 2], [79, 1, 60, 8, 2, 55, 2], [0, 1, 0, 1, 0, 0, 0], [83, 2, 0, 1, 1, 0, 1], [0, 0, 60, 8, 2, 55, 2], [0, 2, 0, 1, 2, 48, 2], [84, 3, 69, 5, 3, 57, 3], [0, 1, 0, 1, 1, 0, 1], [84, 2, 69, 5, 2, 57, 2], [83, 1, 69, 5, 1, 57, 1], [84, 2, 69, 5, 2, 57, 2], [79, 1, 69, 5, 1, 57, 1], [0, 1, 0, 1, 1, 0, 1], [83, 2, 69, 5, 2, 57, 2], [0, 2, 0, 1, 2, 50, 2], [81, 2, 67, 1, 2, 55, 2], [0, 1, 0, 1, 1, 0, 1], [81, 2, 67, 1, 2, 55, 2], [83, 1, 67, 1, 1, 55, 1], [84, 2, 67, 1, 2, 55, 2], [83, 2, 67, 1, 2, 55, 2], [0, 1, 0, 1, 1, 0, 1], [83, 2, 67, 1, 2, 55, 2], [0, 2, 0, 1, 2, 48, 2], [81, 3, 65, 1, 3, 53, 3], 

In [5]:
print("X shape:", X_tensor.shape)
print("X sample:", X_tensor[0])

X shape: torch.Size([34, 25])
X sample: tensor([1.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 1.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 1.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 1.0000, 0.1667, 1.0000, 0.1186])


In [6]:
print("min target:", Y_tensor.min().item())
print("unique values:", torch.unique(Y_tensor))

min target: 0
unique values: tensor([  0,   1,   2,   3,   4,   5,   6,   7,   8,   9,  10,  11,  12,  16,
         22,  31,  35,  38,  43,  44,  45,  46,  47,  48,  49,  50,  51,  52,
         53,  54,  55,  56,  57,  58,  59,  62,  63,  64,  65,  66,  67,  68,
         69,  70,  71,  72,  73,  75,  76,  77,  78,  79,  80,  81,  82,  83,
         84,  85,  86,  87,  88,  89,  90,  91,  92,  93,  94,  95,  96, 100,
        102, 130, 202, 302])


In [9]:
import torch

torch.save({
    "X": X_tensor,
    "Y": Y_tensor,
    "lengths": lengths
}, "DIVA_dataset.pt")

## 전처리 끝!